In [16]:
import geopandas as gpd
import pandas as pd
import classes.entropycalculator as ec
from spatialentropy import altieri_entropy, leibovici_entropy
from scipy.stats import entropy
import numpy as np


import plotly.express as px

scale = "wijken"
amenity_cat = 1
filterlevel = 2

In [17]:
def _get_shannon_entropy(labels, base=2):
    # get the total count of the labels
    total_count = len(labels)
    # get the unique labels and their counts
    _, label_counts = np.unique(labels, return_counts=True)

    probs = label_counts / total_count
    # get the entropy
    return entropy(probs, base=base)

def gm_total_amenities_entropy(gm_name, filter_i):
    L0_BLACKLIST, L1_BLACKLIST = ec.getfilter(filter_i)
    amenity_gdf = gpd.read_parquet(f"data/gm_amenities/amenities_{gm_name}.parquet")
    
    # apply filters
    amenity_gdf = amenity_gdf[~amenity_gdf.L0_category.isin(L0_BLACKLIST)]
    if L1_BLACKLIST:
        for key, value in L1_BLACKLIST.items():
            amenity_gdf = amenity_gdf[
                ~(
                    (amenity_gdf.L0_category == key)
                    & (amenity_gdf.L1_category.isin(value))
                )
            ]
    
    # total number of amenities
    total_amenities = len(amenity_gdf)
    
    
    
    # calculate entropy
    L = amenity_gdf.loc[:, f"L{amenity_cat}_category"].values
    entropy = _get_shannon_entropy(L, base=2)
    
    return total_amenities, entropy

def calc_relative_entropy(row, E, T):
    e_i = row[f"L{amenity_cat}_shannon"]
    t_i = row[f"total_L{amenity_cat}"]
    
    return (t_i * (E - e_i)) / (E * T)

$$E_i = \sum^{n}_{i=1}\frac{t_i(E-e_i)}{ET}$$

In [18]:
# set params and load data
gm = "Amsterdam"

gdf = gpd.read_parquet(f"results/filter{filterlevel}/{scale}/{gm}_{scale}_{filterlevel}.parquet")

amenity_count_gm, entropy_gm = gm_total_amenities_entropy(gm, filterlevel)

# count total amenities
gdf.loc[:, f"total_L{amenity_cat}"] = gdf.loc[:, [col for col in gdf.columns if f"L{amenity_cat}_c" in col]].sum(axis=1)

# calculate relative entropy
gdf.loc[:, "relative_entropy"] = gdf.apply(lambda row: calc_relative_entropy(row, entropy_gm, amenity_count_gm), axis=1)

# sum of relative entropy
summed = gdf.loc[:, "relative_entropy"].sum()

# plot the map
fig = px.choropleth(
    gdf,
    geojson=gdf.geometry,
    locations=gdf.index,
    color="relative_entropy",
    color_continuous_scale="Viridis",
    title=f"Relative Entropy of L{amenity_cat} categories in {gm}: {summed}",
    hover_data={"wijknaam": True, f"total_L{amenity_cat}": True}
)
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":1,"t":50,"l":1,"b":1})
fig.show()

In [19]:
# set params and load data
gm = "Eindhoven"

gdf = gpd.read_parquet(f"results/filter{filterlevel}/{scale}/{gm}_{scale}_{filterlevel}.parquet")

amenity_count_gm, entropy_gm = gm_total_amenities_entropy(gm, filterlevel)

# count total amenities
gdf.loc[:, f"total_L{amenity_cat}"] = gdf.loc[:, [col for col in gdf.columns if f"L{amenity_cat}_c" in col]].sum(axis=1)

# calculate relative entropy
gdf.loc[:, "relative_entropy"] = gdf.apply(lambda row: calc_relative_entropy(row, entropy_gm, amenity_count_gm), axis=1)

# sum of relative entropy
summed = gdf.loc[:, "relative_entropy"].sum()

# plot the map
fig = px.choropleth(
    gdf,
    geojson=gdf.geometry,
    locations=gdf.index,
    color="relative_entropy",
    color_continuous_scale="Viridis",
    title=f"Relative Entropy of L{amenity_cat} categories in {gm}: {summed}",
    hover_data={"wijknaam": True, f"total_L{amenity_cat}": True}
)
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":1,"t":50,"l":1,"b":1})
fig.show()

In [20]:
# set params and load data
gm = "Rotterdam"

gdf = gpd.read_parquet(f"results/filter{filterlevel}/{scale}/{gm}_{scale}_{filterlevel}.parquet")

amenity_count_gm, entropy_gm = gm_total_amenities_entropy(gm, filterlevel)

# count total amenities
gdf.loc[:, f"total_L{amenity_cat}"] = gdf.loc[:, [col for col in gdf.columns if f"L{amenity_cat}_c" in col]].sum(axis=1)

# calculate relative entropy
gdf.loc[:, "relative_entropy"] = gdf.apply(lambda row: calc_relative_entropy(row, entropy_gm, amenity_count_gm), axis=1)

# sum of relative entropy
summed = gdf.loc[:, "relative_entropy"].sum()

# plot the map
fig = px.choropleth(
    gdf,
    geojson=gdf.geometry,
    locations=gdf.index,
    color="relative_entropy",
    color_continuous_scale="Viridis",
    title=f"Relative Entropy of L{amenity_cat} categories in {gm}: {summed}",
    hover_data={"wijknaam": True, f"total_L{amenity_cat}": True}
)
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":1,"t":50,"l":1,"b":1})
fig.show()